# LSTM

In [ ]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import MinMaxScaler 
from keras.models import Sequential,load_model#线性神经网络
from keras.layers.core import Dense,Activation,Dropout#神经网络的激活函数
from keras.optimizers import SGD
import numpy as numpy
import matplotlib.pyplot as plt
from keras.layers.recurrent import LSTM

In [ ]:
security='000001.XSHG'
df=get_price(security, start_date=None, end_date='2020-12-10', frequency='daily', fields=['open', 'close', 'low', 'high', 'volume', 'money',  'pre_close', ], 
          skip_paused=False, fq='pre', count=1500, panel=True)
df['rate']=(df['close']/df['pre_close']-1)*100
df.head()

In [ ]:
# 数据处理
face_back=10
def Processing_data(array,face_back=5):
    data=list()
    for i in range(len(array)-face_back):
        a=list(array[i:i+face_back].values)
        data.append(a)
    return np.array(data)

In [ ]:
array=df['rate']
x=Processing_data(array,face_back)
y=array.values[face_back:]

In [ ]:
X=np.expand_dims(x, axis=1)#增加数据维度，LSTM神经网络维度至少为3维
X.shape

In [ ]:
# 分割数据为训练集和测试集
train_X,test_X=X[:1000,:,:],X[1000:,:,:]
train_y,test_y=y[:1000,],y[1000:,]

In [ ]:
# 搭建LSTM模型
def build_STLM():
    model = Sequential()
    model.add(LSTM(25, input_shape=(train_X.shape[1], train_X.shape[2]),return_sequences=True))
    model.add(LSTM(48))

In [ ]:
# fit network
model=build_STLM()
history = model.fit(X, y, epochs=50, batch_size=300, validation_split=0.25, verbose=1,shuffle=True)

In [ ]:
# 绘制损失图
plt.plot(history.history['loss'], label='train')
plt.plot(history.history['val_loss'], label='test')
plt.title('LSTM_600000.SH', fontsize='12')
plt.ylabel('loss', fontsize='10')

## 数据标准化后的模型

In [ ]:
pre_data=pd.DataFrame()
pre_data['y']=y
prediction5=model.predict(X)
pre_data['prediction5']=prediction5

In [ ]:
# 进行归一化处理
from sklearn.preprocessing import StandardScaler
minmax=StandardScaler()
minmax.fit(np.array(df['rate']).reshape(1500,1))
df['ration']=minmax.transform(np.array(df['rate']).reshape(len(df),1))
x_scaler=Processing_data(df['ration'],face_back)
y_scaler=df['ration'].values[face_back:]
X_scaler=np.expand_dims(x_scaler, axis=1)#增加维度

In [ ]:
# fit network
model2=build_STLM()
history = model2.fit(X, y, epochs=50, batch_size=300, validation_split=0.25, verbose=1,shuffle=True)

In [ ]:
predict6=model2.predict(X_scaler)
prediction6=minmax.inverse_transform(predict6)
pre_data['prediction6']=prediction6

In [ ]:
def draw_Distribution_map(data=pre_data,col='y'):
    cats=pd.cut(data[col],bins=100).value_counts(sort=False)
    cats.plot(kind='bar',title='%s的区间频数统计'%(col),figsize=(8,5))
    new_xticks=np.linspace(0,99,10)
    atick=[cats.index[int(x)] for x in new_xticks]

In [ ]:
# 查看预测值分布
draw_Distribution_map(data=pre_data,col='prediction5')

In [ ]:
#查看预测值分布图
draw_Distribution_map(data=pre_data,col='prediction6')

In [ ]:
#MSE均方误差
from sklearn.metrics import mean_squared_error
#MAEX
from sklearn.metrics import mean_absolute_error
#R^2决定系数

In [ ]:
valuetion(model='model5',col='prediction5')
valuetion(model='model6',col='prediction6')